<a href="https://colab.research.google.com/github/MoSkibidi/The_Art_Of_Computer_System/blob/main/lib_System.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# ไลบรารีระบบ

ในปฏิบัติการนี้เราจะลองสร้างบริการพื้นฐานให้กับผู้พัฒนาแอปพลิเคชันในรูปของไลบรารีระบบ (system library) ซึ่งจัดเป็นหน้าที่หนึ่งของระบบปฏิบัติการ ฟังก์ชันในไลบรารีทั้งหมดจะพัฒนาขึ้นด้วยภาษา Joy

ดาวน์โหลดไลบรารีที่ต้องใช้งานด้วยโค้ดด้านล่าง โค้ดที่เตรียมไว้ให้มีคลาส Joy30 รวมอยู่ด้วย ซึ่งนำมาใช้คอมไพล์โค้ดที่เขียนขึ้นตามข้อกำหนดของภาษา Joy 3.0 ได้ทันที (หากต้องการนิสิตสามารถแก้ไขโค้ดให้ดาวน์โหลด Joy 3.0 ของตนเองมาใช้ได้)

In [1]:
%%capture
!pip install lark-parser
!rm -rf comp-sys-public-lib
!wget -q -O - https://ecourse.cpe.ku.ac.th/courses/comsys/lib/ch11.tgz | tar zxf -
!pip install -e comp-sys-public-lib
!pip install -e comp-sys-public-lib/modules/component-builder
import site; site.main()
from course_ch11_init import *

def compile_and_runsim(code, super_fast=False):
    assemble_and_simulate(Joy30().compile(code), super_fast=super_fast)

In [ ]:
run_test(TestJoy30)

............................................................
----------------------------------------------------------------------
Ran 60 tests in 8.618s

OK


นิยามคลาส `TestLibBase` เอาไว้เพื่อนำไปสร้างเป็นตัวทดสอบในภายหลัง

In [ ]:
class TestLibBase(unittest.TestCase):

    JOY_COMPILER = Joy30
    LIBS = Joy30.RUNTIME

    def setUp(self):
        self.cpu = PureHackCPU()
        if self.JOY_COMPILER is None:
            raise Exception('Please define "JOY_COMPILER" as a class member.')

    def compile_and_run(self, code, max_steps=100000):
        self.cpu.reset()
        asm = self.JOY_COMPILER().compile(self.LIBS + code)
        instrs = assemble(asm)
        self.cpu.load_instructions(instrs)
        self.cpu.run(max_steps, output_traces=False, until_pc=len(instrs))

# บริการอินพุทเอาท์พุทพื้นฐาน

เราจะเริ่มต้นด้วยการจำลองบริการของระบบอินพุทเอาท์พุทเบื้องต้น (Basic Input/Output System - BIOS) ของไมโครคอมพิวเตอร์ โดยสร้างฟังก์ชันที่ให้บริการด้านการแสดงผลและการอ่านคีย์บอร์ดเบื้องต้น ซึ่งประกอบไปด้วยฟังก์ชันดังนี้

* ฟังก์ชัน `draw_glyph(x,y,glyph)` แสดงอักขระแบบบิตแมปขนาด 16x16 จุด ตามที่ระบุไว้ในอาร์เรย์ `glyph` บนหน้าจอ ณ คอลัมน์​ `x` และแถว `y` โดยแบ่งพื้นที่การแสดงผลอักขระออกเป็น 16 แถว แถวละ 32 คอลัมน์ เริ่มต้นจากแถวที่ 0 และคอลัมน์ที่ 0 (มุมบนซ้าย) และสุดที่แถวที่ 15 คอลัมน์ที่ 31 ดังภาพ
```
(0,0)
  +------------------+
  |                  |
  |      Screen      |
  |                  |
  +------------------+
                  (31,15)
```
* ฟังก์ชัน `scroll(num)` ใช้ในการเลื่อนหน้าจอขึ้นตามจำนวนแถวที่ระบุไว้ใน `num`
* ฟังก์ชัน `read_key()` รอจนกว่าจะมีการกดคีย์ใด ๆ แล้วคืนค่าคีย์ที่กด

In [ ]:
LIB_BIOS = '''
///////////////////////////////////////////////////////////////////////////
// Display bitmap in the array glyph on the screen at text position (x,y).
///////////////////////////////////////////////////////////////////////////
def draw_glyph(x, y, glyph) {
    let count = 0;
    let pos = y*16*32+x;
    while count < 16 {
        let *(0x4000+pos) = *(glyph+count);
        let count = count + 1;
        let pos = pos + 32;
    }
}

///////////////////////////////////////////////////////////////////////////
// Scroll the text screen by num lines
///////////////////////////////////////////////////////////////////////////
def scroll(num) {
    let offset = num*16*32;
    let start = 0x4000 + offset;
    let current = start;
    while current < 0x6000 {
        let *(current-offset) = *current;
        let current = current + 1;
        let *10 = current;
    }
    let current = current - offset;
    while current < 0x6000 {
        let *current = 0;
        let current = current + 1;
    }
}

///////////////////////////////////////////////////////////////////////////
// Wait until a key is pressed, then return its key code.
///////////////////////////////////////////////////////////////////////////
def read_key() {
    while *0x6000 {} // if a key is currently pressed, wait until it is released
    until *0x6000 {} // wait until a key is pressed
    return *0x6000;
}
'''

# บิตแมปฟอนต์
ฟังก์ชัน `draw_glyph()` ควรใช้งานร่วมกับบิตแมปฟอนต์ที่นิยามเอาไว้ล่วงหน้า ให้ดาวน์โหลดไฟล์ `font.joy` ซึ่งนิยามฟอนต์ที่ช่วยกันออกแบบขึ้นมาไว้เป็นตัวแปรโกลบอล `FONT` ในรูปอาร์เรย์ของอาร์เรย์ในภาษา Joy จากนั้นรันโค้ดด้านล่างเพื่อโหลดโค้ดมาเก็บไว้ในตัวแปร `LIB_FONT` เพื่อนำไปใช้ต่อไป

In [ ]:
# ดาวน์โหลดฟอนต์จากไฟล์ที่ทั้งคลาสช่วยกันสร้างขึ้นมา
!rm -f font.joy
!wget -q - https://ecourse.cpe.ku.ac.th/courses/comsys/2567f/font.joy

LIB_FONT = open('font.joy').read()

ลองนำอักขระในตารางแอสกี้ตั้งแต่ 32-126 มาแสดงผลบนหน้าจอ กดคีย์ใด ๆ (บนซิมูเลชัน) เพื่อเลื่อนหน้าจอขึ้นทีละบรรทัด

In [ ]:
LIBS = Joy30.RUNTIME + LIB_FONT + LIB_BIOS

test_bios = '''
    let x = 0;
    let y = 5;
    let char = 32;
    until char > 126 {
        draw_glyph(x, y, *(FONT+char-32));
        let char = char + 1;
        let x = x+1;
        if x > 31 {
            let x = 0;
            let y = y + 1;
        }
    }

    while 1 {
        read_key(); // รอกดคีย์
        scroll(1); // เลื่อนจอขึ้น 1 บรรทัด
    }
'''

compile_and_runsim(LIBS+test_bios, super_fast=True)

# ไลบรารี stdlib (Standard Lib)

ไลบรารี stdlib นิยามฟังก์ชันพื้นฐานที่ใช้งานบ่อยครั้งในโปรแกรมทั่วไป อาทิเช่น การจองหน่วยความจำ การแปลงข้อมูลจากตัวเลขเป็นสตริง หรือกลับกัน

สิ่งที่เราจะนำมาทดลองสร้างคือฟังก์ชันที่แปลงตัวเลขเป็นสตริง `itoa()`
* ฟังก์ชัน `itoa(num)` คืนค่าตำแหน่งของสตริงที่เก็บผลลัพธ์การแปลงค่าของ `num` เป็นสตริง

In [ ]:
LIB_STDLIB = '''
def itoa(num) {
    let buf = "XXXXXX"; // allowed numbers have max length of 6 chars
    let ptr = buf;
    if num == 0 {
        let *ptr = '0';
        let *(ptr+1) = 0;
        return buf;
    }
    if num < 0 {
        let *ptr = '-';
        let ptr = ptr+1;
        let num = -num;
    }
    let div = 10000;
    until num/div {
        let div = div/10;
    }
    while div {
        let digit = num/div;
        let *ptr = '0' + digit;
        let ptr = ptr + 1;
        let num = num%div;
        let div = div/10;
    }
    let *ptr = 0;
    return buf;
}
'''

รันตัวทดสอบไลบรารี stdlib

In [ ]:
class TestStdLib(TestLibBase):

    LIBS = Joy30.RUNTIME + LIB_STDLIB

    def base_test_itoa(self,num):
        self.compile_and_run(f'''
            let *10 = itoa({num});
        ''', max_steps=1000000)
        num_digits = len(str(num))
        ptr = self.cpu.ram[10]
        self.assertEqual(
            self.cpu.ram[ptr:ptr+num_digits+1],
            [ord(x) for x in str(num)] + [0])

    def test_itoa(self):
        self.base_test_itoa(0)
        self.base_test_itoa(12)
        self.base_test_itoa(132)
        self.base_test_itoa(5621)
        self.base_test_itoa(32767)
        self.base_test_itoa(-4)
        self.base_test_itoa(-652)
        self.base_test_itoa(-1937)
        self.base_test_itoa(-32768)

run_test(TestStdLib)

.
----------------------------------------------------------------------
Ran 1 test in 2.443s

OK


# ไลบรารี stdio (Standard Input/Output)
ไลบรารี stdio นิยามฟังก์ชันสำหรับการติดต่อกับอินพุทและเอาท์พุทมาตรฐานในรูปของ stream ซึ่งในระบบปฏิบัติการทั่วไปนั้นจะรวมถึงคีย์บอร์ด หน้าจอ ไฟล์ เครือข่าย และอุปกรณ์ต่อพ่วงอื่น ๆ

ในส่วนของรายวิชาเราจะทดลองสร้างฟังก์ชันที่ส่งข้อมูลไปยังหน้าจอเท่านั้น โดยสมมติให้บนหน้าจอมี*เคอร์เซอร์* ที่ระบุตำแหน่งที่จะใช้แสดงผลข้อความถัดไป ไลบรารี stdio ของเราประกอบไปด้วยฟังก์ชันดังนี้

* ฟังก์ชัน `putc(c)` ในกรณีที่ `c` มีค่าอยู่ระหว่าง 32 ถึง 126 ให้แสดงอักขระตามรหัสแอสกี้ของค่า `c` บนหน้าจอ ณ ตำแหน่งเคอร์เซอร์ปัจจุบัน พร้อมทั้งเลื่อนเคอร์เซอร์ไปข้างหน้า 1 ตำแหน่ง ส่วนค่า `c` อื่น ๆ ให้ดำเนินการดังนี้
    * หากค่า `c` เท่ากับ 10 (line feed - LF) ให้เลื่อนเคอร์เซอร์ลง 1 บรรทัด โดยไม่ต้องเลื่อนเคอร์เซอร์กลับไปต้นบรรทัด
    * หากค่า `c` เท่ากับ 13 (carriage return - CR) ให้เลื่อนเคอร์เซอร์กลับไปต้นบรรทัด โดยไม่ต้องเลื่อนเคอร์เซอร์ลง
    * หากค่า `c` เป็นค่าอื่น ไม่ต้องดำเนินการใด ๆ
* ฟังก์ชัน `print(s)` พิมพ์ข้อความในสตริง `s` ณ ตำแหน่งเคอร์เซอร์ พร้อมเลื่อนเคอร์เซอร์ไปท้ายข้อความ
* ฟังก์ชัน `println(s)` ทำงานเหมือนฟังก์ชัน `print()` แต่เมื่อแสดงข้อความแล้วให้เลื่อนเคอร์เซอร์กลับไปต้นบรรทัดและเลื่อนลง 1 บรรทัด
* ฟังก์ชัน `clrscr()` เคลียร์หน้าจอ และนำเคอร์เซอร์ไปวางไว้ที่ตำแหน่ง (0,0)

พฤติกรรมของเคอร์เซอร์เป็นดังนี้
* เมื่อมีการเลื่อนเคอร์เซอร์ไปข้างหน้า 1 ตำแหน่ง หากเคอร์เซอร์ตกขอบขวาของจอ ให้เลื่อนเคอร์เซอร์กลับไปต้นบรรทัดและเลื่อนลง 1 บรรทัด
* หากเคอร์เซอร์ตกขอบล่างของจอ ให้เลื่อนจอ (scroll) ขึ้น 1 บรรทัด (คำใบ้: ฟังก์ชัน scroll นิยามไว้ให้ด้านบนแล้ว)

In [ ]:
# DO NOT ERASE THIS CELL - to be graded

LIB_STDIO = '''
// นิยามตัวแปรโกลบอลที่ต้องใช้ตามต้องการ
let cursor_x = 0;
let cursor_y = 0;

/////////////////////////////////////////////////////////////
def putc(c) {
    global FONT ;
    global cursor_x ;
    global cursor_y ;
    if (c >= 32 && c <= 126) {
        draw_glyph(cursor_x, cursor_y, *(FONT+c-32));
        let cursor_x = cursor_x + 1;
    }
    if (c == 10) {
        let cursor_y = cursor_y + 1;
    }
    if (c == 13) {
        let cursor_x = 0;
    }

    if (cursor_x > 31) {
        let cursor_x = 0;
        let cursor_y = cursor_y + 1;
    }

    if (cursor_y > 15) {
        scroll(1);
        let cursor_y = 15;
    }
}

/////////////////////////////////////////////////////////////
def print(s) {
    let count = 0;
    while *(s+count) {
        let c = *(s+count);
        putc(c);
        let count = count + 1;
    }
}

/////////////////////////////////////////////////////////////
def println(s) {
    print(s);
    putc(10);
    putc(13);

}

/////////////////////////////////////////////////////////////
def clrscr() {
    global cursor_x ;
    global cursor_y ;
    global FONT ;
    let cursor_x = 0;
    let cursor_y = 0;
    while cursor_y < 16 {
        draw_glyph(cursor_x, cursor_y, *(FONT+' '-32));
        let cursor_x = cursor_x+1;
        if cursor_x > 31 {
            let cursor_x = 0;
            let cursor_y = cursor_y + 1;
        }
    }
    let cursor_x = 0;
    let cursor_y = 0;

}
'''

## ตัวอย่างโค้ดส่งท้าย

โค้ดด้านล่างควรให้ผลลัพธ์บนหน้าจอดังนี้
```
   A
    B
D    C
```

In [ ]:
LIBS = Joy30.RUNTIME + LIB_FONT + LIB_BIOS + LIB_STDLIB + LIB_STDIO

test_stdio = '''
  putc(' '); putc(' '); putc(' '); putc('A');
  putc(10); putc('B');
  putc(10); putc('C');
  putc(13); putc('D');
'''

compile_and_runsim(LIBS+test_stdio, super_fast=True)

โค้ดด้านล่างต้องแสดงข้อความ `Hello, World!` ออกทางหน้าจอ

In [ ]:
LIBS = Joy30.RUNTIME + LIB_FONT + LIB_BIOS + LIB_STDLIB + LIB_STDIO

hello_world = '''
    println("Hello, World!");
'''

compile_and_runsim(LIBS+hello_world, super_fast=True)

โค้ดด้านล่างต้องแสดงอักขระตามรหัสแอสกี้ 32 ถึง 126 ทั้งหมด (ยกเว้นอักขระ ") โดยขึ้นบรรทัดใหม่และเลื่อนหน้าจอได้อย่างถูกต้อง

In [ ]:
LIBS = Joy30.RUNTIME + LIB_FONT + LIB_BIOS + LIB_STDLIB + LIB_STDIO

long_line = r'''
    let line = " !#$%&'()*+,-./0123456789:;<=>?@ABCDEFGHIJKLMNOPQRSTUVWXYZ[\]^_`abcdefghijklmnopqrstuvwxyz{|}~";
    while 1 {
        print(line);
    }
'''

compile_and_runsim(LIBS+long_line, super_fast=True)

โค้ดด้านล่างต้องแสดงข้อความ `Hello, World!` ทีละบรรทัดเมื่อมีการกดคีย์ space พร้อมแสดงหมายเลขบรรทัด และจะเคลียร์หน้าจอเมื่อกดคีย์ enter

In [ ]:
LIBS = Joy30.RUNTIME + LIB_FONT + LIB_BIOS + LIB_STDLIB + LIB_STDIO

hello_world_count = '''
    let line = 1;
    while 1 {
        let key = read_key();
        if key == 32 { // space is pressed
            print("Hello, World! ");
            println(itoa(line));
            let line = line + 1;
        }
        if key == 128 { // enter is pressed
            clrscr();
        }
    }
'''

compile_and_runsim(LIBS+hello_world_count, super_fast=True)